In [1]:
# Common imports
import io
import json
from PIL import Image

# Celery imports
import msgpack
from celery import Celery

# Custom imports
import unibox
from comfyui_router.utils import extract_images_from_response

# Import the task module explicitly to ensure the task is registered
import comfyui_router.tasks
from comfyui_router.tasks import process_request


MQ_IP = "52.10.216.28"

## Setup Comfy

start comfyui:

```bash
COMFY_DIR = "/rmt/yada/apps/comfyui"
OUTPUT_DIR = "/lv0/comfy_outs"
START_PORT = 18188
CUDA_DEVICES = [0, 1, 2, 3, 4, 5, 6, 7]

cd $COMFY_DIR

for CUDA_DEVICE in $CUDA_DEVICES
    python main.py  --output-directory $OUTPUT_DIR --port $START_PORT --cuda-device $CUDA_DEVICE &


```

In [4]:
COMFY_DIR = "/rmt/yada/apps/comfyui"
OUTPUT_DIR = "/lv0/comfy_outs"
START_PORT = 18188
CUDA_DEVICES = [0, 1, 2, 3, 4, 5, 6, 7]


for device in CUDA_DEVICES:
    port = START_PORT + device
    command = f"python {COMFY_DIR}/main.py --port {port} --cuda-device {device} --output-dir {OUTPUT_DIR}"
    print(command)

python /rmt/yada/apps/comfyui/main.py --port 18188 --cuda-device 0 --output-dir /lv0/comfy_outs
python /rmt/yada/apps/comfyui/main.py --port 18189 --cuda-device 1 --output-dir /lv0/comfy_outs
python /rmt/yada/apps/comfyui/main.py --port 18190 --cuda-device 2 --output-dir /lv0/comfy_outs
python /rmt/yada/apps/comfyui/main.py --port 18191 --cuda-device 3 --output-dir /lv0/comfy_outs
python /rmt/yada/apps/comfyui/main.py --port 18192 --cuda-device 4 --output-dir /lv0/comfy_outs
python /rmt/yada/apps/comfyui/main.py --port 18193 --cuda-device 5 --output-dir /lv0/comfy_outs
python /rmt/yada/apps/comfyui/main.py --port 18194 --cuda-device 6 --output-dir /lv0/comfy_outs
python /rmt/yada/apps/comfyui/main.py --port 18195 --cuda-device 7 --output-dir /lv0/comfy_outs


## celery

In [3]:
# Initialize Celery client to connect to the broker
app = Celery('tasks', broker=f'pyamqp://runner:UjLyQtRMWTG68aAKecq4Hn@{MQ_IP}//', backend='rpc://')

# JSON string to be sent
json_string = '{"6": {"inputs": {"text": "isekai joucho, 1girl, very long hair, best quality", "clip": ["101", 1]}, "class_type": "CLIPTextEncode", "_meta": {"title": "POSITIVE"}}, "7": {"inputs": {"text": "lowres, worst quality, displeasing, bad quality, bad anatomy, text, error, extra digit, cropped, average quality", "clip": ["101", 1]}, "class_type": "CLIPTextEncode", "_meta": {"title": "NEGATIVE"}}, "101": {"inputs": {"ckpt_name": "yada_checkpoints/qft_v5c-c53_v5c-logfav-9.6_60k_cont1/checkpoint-e17_s5000.safetensors"}, "class_type": "CheckpointLoaderSimple", "_meta": {"title": "Load Checkpoint"}}, "103": {"inputs": {"filename_prefix": "ComfyUI", "images": ["34:4", 0]}, "class_type": "SaveImage", "_meta": {"title": "Save Image"}}, "34:0": {"inputs": {"width": 896, "height": 1152, "batch_size": 4}, "class_type": "EmptyLatentImage", "_meta": {"title": "Empty Latent Image"}}, "34:1": {"inputs": {"multiplier": 0.75, "model": ["101", 0]}, "class_type": "RescaleCFG", "_meta": {"title": "RescaleCFG"}}, "34:2": {"inputs": {"sampling": "v_prediction", "zsnr": true, "model": ["34:1", 0]}, "class_type": "ModelSamplingDiscrete", "_meta": {"title": "ModelSamplingDiscrete"}}, "34:3": {"inputs": {"seed": 432737405573798, "steps": 28, "cfg": 5.5, "sampler_name": "euler", "scheduler": "normal", "denoise": 1, "model": ["34:2", 0], "positive": ["6", 0], "negative": ["7", 0], "latent_image": ["34:0", 0]}, "class_type": "KSampler", "_meta": {"title": "KSampler"}}, "34:4": {"inputs": {"samples": ["34:3", 0], "vae": ["101", 2]}, "class_type": "VAEDecode", "_meta": {"title": "VAE Decode"}}}'
json_data = json.loads(json_string)

# Unique key for the request
unique_key = "debug_request_001"

# Send the request to the Celery worker
result = app.send_task('comfyui_router.tasks.process_request', args=[unique_key, json_data])

# Wait for the result (blocking)
packed_response = result.get(timeout=40)  # You can adjust the timeout as needed

# Decode the MessagePack response
unique_key, raw_response = msgpack.unpackb(packed_response, raw=False)

In [2]:
str(True)

'True'

In [6]:
node_imgs = extract_images_from_response(raw_response)
node_imgs

{'103': [<PIL.PngImagePlugin.PngImageFile image mode=RGB size=896x1152>,
  <PIL.PngImagePlugin.PngImageFile image mode=RGB size=896x1152>,
  <PIL.PngImagePlugin.PngImageFile image mode=RGB size=896x1152>,
  <PIL.PngImagePlugin.PngImageFile image mode=RGB size=896x1152>]}

In [8]:
from dataproc4.utils.image_utils import concatenate_images_horizontally

concatenate_images_horizontally(node_imgs['103'])